In [1]:
import cv2
import numpy as np
import os

# Output directory for frames
output_dir = "./color_frames/"
os.makedirs(output_dir, exist_ok=True)  # Ensure directory exists

# Load the video
cap = cv2.VideoCapture("./test.mp4")
if not cap.isOpened():
    print("Error: Could not open video file.")
    exit()

frame_count = 0
while True:
    frame_ready, frame = cap.read()  # Read the frame
    if not frame_ready:
        print("End of video or error reading frame.")
        break

    # Save color frame as a NumPy array (in BGR format)
    frame_path = os.path.join(output_dir, f"frame_{frame_count:04d}.npy")
    np.save(frame_path, frame)

    frame_count += 1

    # Show progress
    print(f"Processed frame {frame_count}")

    # Exit on key press (optional)
    if cv2.waitKey(10) == 27:  # Escape key
        break

cap.release()
print(f"Color frames saved in directory: {output_dir}")


Processed frame 1
Processed frame 2
Processed frame 3
Processed frame 4
Processed frame 5
Processed frame 6
Processed frame 7
Processed frame 8
Processed frame 9
Processed frame 10
Processed frame 11
Processed frame 12
Processed frame 13
Processed frame 14
Processed frame 15
Processed frame 16
Processed frame 17
Processed frame 18
Processed frame 19
Processed frame 20
Processed frame 21
Processed frame 22
Processed frame 23
Processed frame 24
Processed frame 25
Processed frame 26
Processed frame 27
Processed frame 28
Processed frame 29
Processed frame 30
Processed frame 31
Processed frame 32
Processed frame 33
Processed frame 34
Processed frame 35
Processed frame 36
Processed frame 37
Processed frame 38
Processed frame 39
Processed frame 40
Processed frame 41
Processed frame 42
Processed frame 43
Processed frame 44
Processed frame 45
Processed frame 46
Processed frame 47
Processed frame 48
Processed frame 49
Processed frame 50
Processed frame 51
Processed frame 52
Processed frame 53
Pr

In [1]:
import os
import ffmpeg
import cv2
import numpy as np
from PIL import Image, ImageDraw, ImageFont

# --------------------------
# Adjustable Global Settings
# --------------------------
COLOR_FRAMES_DIR       = "color_frames"       # Directory with .npy color frames (BGR)
ASCII_FRAMES_DIR       = "ascii_frames_color" # Where ASCII PNG frames will be stored
OUTPUT_AUDIO_PATH      = "extracted_audio.mp3" # If you want to extract audio from a video
OUTPUT_VIDEO_SILENT    = "ascii_silentColour.mp4"    # Silent ASCII video output
FINAL_OUTPUT_VIDEO     = "ascii_colored_final.mp4"

# If you want to extract audio from a specific video, put its path here
INPUT_VIDEO_PATH       = "test.mp4"            # Used only if you want to extract audio

# Font settings
FONT_PATH              = None  # e.g. "/usr/share/fonts/truetype/dejavu/DejaVuSansMono.ttf"
FONT_SIZE              = 12

# ASCII chars from light to dark
ASCII_CHARS           = " .:-=+*#%@"

# Desired character width (in ASCII columns)
ASCII_WIDTH           = 360  
# Maximum ASCII height (to avoid huge images if aspect ratio is extreme)
ASCII_MAX_HEIGHT      = 240

# Target frame rate for final ASCII video
TARGET_FPS            = 23.5


# ----------------------------------------------------------------------------
# 1. (Optional) Extract Audio from an Existing Video
# ----------------------------------------------------------------------------
def extract_audio_ffmpeg(input_video_path, output_audio_path):
    """
    Extracts audio from 'input_video_path' and saves it as 'output_audio_path' (MP3).
    """
    if not os.path.exists(input_video_path):
        print(f"[WARN] Video file '{input_video_path}' not found. Skipping audio extraction.")
        return
    try:
        (
            ffmpeg
            .input(input_video_path)
            .output(output_audio_path, format="mp3", acodec="mp3")
            .run(overwrite_output=True, quiet=True)
        )
        print(f"[INFO] Audio extracted to: {output_audio_path}")
    except ffmpeg.Error as e:
        print(f"[ERROR] FFmpeg audio extraction failed: {e}")


# ----------------------------------------------------------------------------
# 2. Convert One Color Frame (BGR) to a Colored ASCII Image
# ----------------------------------------------------------------------------
def frame_to_color_ascii_image(frame_bgr,
                               ascii_chars=ASCII_CHARS,
                               font_path=None,
                               font_size=12,
                               target_width=80,
                               max_height=60):
    """
    Convert a single color frame (NumPy BGR array) to a colored ASCII art image (PIL).
    
    Steps:
      1. Convert BGR -> RGB (for Pillow usage).
      2. Resize image to (target_width, new_height) using cv2.INTER_AREA.
      3. Determine ASCII character by brightness (luma).
      4. Draw each character using its average color from the resized pixel.
      
    :param frame_bgr: NumPy array shape (H, W, 3) in BGR format.
    :return: A PIL.Image in color ASCII.
    """
    # Convert BGR to RGB
    frame_rgb = cv2.cvtColor(frame_bgr, cv2.COLOR_BGR2RGB)
    rows, cols, _ = frame_rgb.shape

    # Estimate new ASCII height from aspect ratio
    # Div factor ~2 because typical ASCII chars are taller than wide
    new_height = int(rows * target_width / (cols * 2))
    new_height = min(new_height, max_height)

    # Resize using INTER_AREA to get "average" color
    resized_rgb = cv2.resize(frame_rgb, (target_width, new_height), interpolation=cv2.INTER_AREA)

    # Compute brightness for ASCII char selection
    # brightness = 0.299*R + 0.587*G + 0.114*B
    r = resized_rgb[:, :, 0].astype(np.float32)
    g = resized_rgb[:, :, 1].astype(np.float32)
    b = resized_rgb[:, :, 2].astype(np.float32)
    brightness = 0.299 * r + 0.587 * g + 0.114 * b

    # Map brightness to an ASCII character
    num_ascii_chars = len(ascii_chars)
    step = max(1, 256 // num_ascii_chars)
    ascii_indices = np.clip((brightness // step).astype(int), 0, num_ascii_chars - 1)

    # Load font
    if font_path:
        try:
            font = ImageFont.truetype(font_path, font_size)
        except IOError:
            print("[WARN] Could not load custom font. Using default.")
            font = ImageFont.load_default()
    else:
        font = ImageFont.load_default()

    char_width, char_height = font.getsize("A")
    image_width = target_width * char_width
    image_height = new_height * char_height

    # Create the final ASCII image (black background)
    image = Image.new("RGB", (image_width, image_height), "black")
    draw = ImageDraw.Draw(image)

    # Write each character in the average color
    for row_i in range(new_height):
        for col_i in range(target_width):
            ascii_char = ascii_chars[ascii_indices[row_i, col_i]]

            # Extract color from the resized RGB pixel
            pixel_r = int(resized_rgb[row_i, col_i, 0])
            pixel_g = int(resized_rgb[row_i, col_i, 1])
            pixel_b = int(resized_rgb[row_i, col_i, 2])

            x_pos = col_i * char_width
            y_pos = row_i * char_height

            draw.text(
                (x_pos, y_pos),
                ascii_char,
                font=font,
                fill=(pixel_r, pixel_g, pixel_b)
            )

    return image


# ----------------------------------------------------------------------------
# 3. Convert NPY Color Frames to Colored ASCII PNGs
# ----------------------------------------------------------------------------
def npy_color_frames_to_ascii_frames(input_npy_dir,
                                     output_ascii_dir,
                                     ascii_chars=ASCII_CHARS,
                                     font_path=None,
                                     font_size=12,
                                     target_width=80,
                                     max_height=60):
    """
    Reads .npy color frames from `input_npy_dir`, converts each to colored ASCII .png,
    and saves in `output_ascii_dir`.
    
    We assume each .npy is shape (H, W, 3) in BGR format.
    """
    os.makedirs(output_ascii_dir, exist_ok=True)

    npy_files = sorted([f for f in os.listdir(input_npy_dir) if f.endswith(".npy")])
    if not npy_files:
        print(f"[ERROR] No .npy files found in {input_npy_dir}.")
        return

    for i, npy_file in enumerate(npy_files):
        path_npy = os.path.join(input_npy_dir, npy_file)
        frame_bgr = np.load(path_npy)  # shape (H, W, 3), BGR

        ascii_img = frame_to_color_ascii_image(
            frame_bgr,
            ascii_chars=ascii_chars,
            font_path=font_path,
            font_size=font_size,
            target_width=target_width,
            max_height=max_height
        )

        # Save as PNG
        output_path = os.path.join(output_ascii_dir, f"frame_{i:05d}.png")
        ascii_img.save(output_path)

        if i % 50 == 0 and i != 0:
            print(f"[INFO] Converted {i} frames to colored ASCII...")

    print(f"[DONE] All NPY color frames converted to ASCII PNG in '{output_ascii_dir}'.")


# ----------------------------------------------------------------------------
# 4. Create a Silent Video from ASCII PNG Frames
# ----------------------------------------------------------------------------
def create_silent_video_from_frames(frames_dir, output_video_path, fps=10):
    """
    Uses OpenCV to read sorted PNG frames from 'frames_dir' and writes out a silent MP4 video.
    """
    frame_files = sorted([f for f in os.listdir(frames_dir) if f.endswith('.png')])
    if not frame_files:
        raise ValueError(f"No PNG frames found in {frames_dir}")

    # Read first frame to get dimensions
    first_frame_path = os.path.join(frames_dir, frame_files[0])
    first_frame = cv2.imread(first_frame_path, cv2.IMREAD_COLOR)
    if first_frame is None:
        raise IOError(f"Could not read the first frame: {first_frame_path}")
    height, width, _ = first_frame.shape

    fourcc = cv2.VideoWriter_fourcc(*"mp4v")
    video_writer = cv2.VideoWriter(output_video_path, fourcc, fps, (width, height))

    for frame_file in frame_files:
        frame_path = os.path.join(frames_dir, frame_file)
        frame = cv2.imread(frame_path, cv2.IMREAD_COLOR)
        if frame is None:
            print(f"[WARN] Skipping unreadable frame: {frame_file}")
            continue
        video_writer.write(frame)

    video_writer.release()
    print(f"[INFO] Silent ASCII video saved to: {output_video_path}")


# ----------------------------------------------------------------------------
# 5. Merge Silent Video and Audio
# ----------------------------------------------------------------------------
def merge_video_audio(video_path, audio_path, output_final_video):
    """
    Merges a silent video file and an audio file into a single MP4 (H.264 + AAC).
    """
    if not os.path.exists(video_path):
        print(f"[ERROR] Silent video '{video_path}' not found.")
        return
    if not os.path.exists(audio_path):
        print(f"[ERROR] Audio file '{audio_path}' not found.")
        return

    try:
        (
            ffmpeg
            .output(ffmpeg.input(video_path), ffmpeg.input(audio_path),
                    output_final_video,
                    vcodec="libx264",    # H.264
                    acodec="aac",        # AAC
                    strict="experimental"
            )
            .run(overwrite_output=True, quiet=True)
        )
        print(f"[INFO] Final video with audio saved to: {output_final_video}")
    except ffmpeg.Error as e:
        print(f"[ERROR] FFmpeg merge failed: {e}")


# ----------------------------------------------------------------------------
# MAIN EXECUTION EXAMPLE
# ----------------------------------------------------------------------------
def main():
    """
    Example pipeline:
      1) (Optional) Extract audio from an original video.
      2) Convert .npy color frames to ASCII PNG frames.
      3) Build a silent ASCII video from those PNGs.
      4) Merge silent ASCII video + extracted audio (if audio exists).
    """
    # 1) Optional: Extract audio from original video (if you want the final to have audio)
    extract_audio_ffmpeg(INPUT_VIDEO_PATH, OUTPUT_AUDIO_PATH)

    # 2) Convert color .npy frames to colored ASCII .png frames
    npy_color_frames_to_ascii_frames(
        input_npy_dir=COLOR_FRAMES_DIR,
        output_ascii_dir=ASCII_FRAMES_DIR,
        ascii_chars=ASCII_CHARS,
        font_path=FONT_PATH,
        font_size=FONT_SIZE,
        target_width=ASCII_WIDTH,
        max_height=ASCII_MAX_HEIGHT
    )

    # 3) Create a silent video from ASCII frames
    create_silent_video_from_frames(
        frames_dir=ASCII_FRAMES_DIR,
        output_video_path=OUTPUT_VIDEO_SILENT,
        fps=TARGET_FPS
    )

    # 4) Merge silent video + MP3 audio
    merge_video_audio(OUTPUT_VIDEO_SILENT, OUTPUT_AUDIO_PATH, FINAL_OUTPUT_VIDEO)

    print("[DONE] Colored ASCII video with audio is available at:", FINAL_OUTPUT_VIDEO)


if __name__ == "__main__":
    main()


[INFO] Audio extracted to: extracted_audio.mp3
[INFO] Converted 50 frames to colored ASCII...
[INFO] Converted 100 frames to colored ASCII...
[INFO] Converted 150 frames to colored ASCII...
[INFO] Converted 200 frames to colored ASCII...
[INFO] Converted 250 frames to colored ASCII...
[INFO] Converted 300 frames to colored ASCII...
[INFO] Converted 350 frames to colored ASCII...
[INFO] Converted 400 frames to colored ASCII...
[INFO] Converted 450 frames to colored ASCII...
[INFO] Converted 500 frames to colored ASCII...
[INFO] Converted 550 frames to colored ASCII...
[INFO] Converted 600 frames to colored ASCII...
[INFO] Converted 650 frames to colored ASCII...
[INFO] Converted 700 frames to colored ASCII...
[INFO] Converted 750 frames to colored ASCII...
[INFO] Converted 800 frames to colored ASCII...
[INFO] Converted 850 frames to colored ASCII...
[INFO] Converted 900 frames to colored ASCII...
[INFO] Converted 950 frames to colored ASCII...
[INFO] Converted 1000 frames to colored AS

In [ ]:
### for web visualizetion we need to perfrom this compression, if you want the best quality dont perform this compression.

In [5]:
import ffmpeg

import os

# Input and output file paths
input_file = 'ascii_colored_final.mp4'  # Replace with your video file
output_file = 'ascii_colored_finalR.mp4'  # Replace with your desired output path


# Desired max size (strictly under 100 MB)
max_size_mb = 100
max_size_bytes = max_size_mb * 1024 * 1024

# Improved compression settings for higher quality
ffmpeg.input(input_file).output(
    output_file,
    vcodec='libx264',    # H.264 codec for wide browser compatibility
    acodec='aac',        # AAC for audio compatibility
    crf=18,              # Higher quality (near lossless)
    preset='slow',       # Higher compression quality at the cost of speed
    maxrate='5M',        # Allow more bitrate for better quality
    bufsize='10M',       # Smoother playback with increased buffer size
    audio_bitrate='128k',  # Explicitly set high-quality audio
    movflags='+faststart'  # Web playback optimization
).run()

# Check if the file is under the size limit
output_size_bytes = os.path.getsize(output_file)
if output_size_bytes > max_size_bytes:
    print(f"Warning: Compressed file size is {output_size_bytes / (1024 * 1024):.2f} MB, exceeding the limit.")
else:
    print(f"Video successfully compressed and saved to: {output_file} (Size: {output_size_bytes / (1024 * 1024):.2f} MB)")

ffmpeg version 4.4.2-0ubuntu0.22.04.1+esm6 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.4.0-1ubuntu1~22.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1+esm6 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enabl

Video successfully compressed and saved to: ascii_colored_finalR.mp4 (Size: 76.81 MB)


[mp4 @ 0x5d3d01cb7f40] Starting second pass: moving the moov atom to the beginning of the file
frame= 3432 fps= 10 q=-1.0 Lsize=   78657kB time=00:02:25.91 bitrate=4416.0kbits/s speed=0.434x    
video:76427kB audio:2136kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 0.119668%
[libx264 @ 0x5d3d01cb8980] frame I:58    Avg QP:32.87  size:236986
[libx264 @ 0x5d3d01cb8980] frame P:969   Avg QP:31.44  size: 43542
[libx264 @ 0x5d3d01cb8980] frame B:2405  Avg QP:36.97  size:  9282
[libx264 @ 0x5d3d01cb8980] consecutive B-frames:  4.5%  5.1%  3.5% 86.9%
[libx264 @ 0x5d3d01cb8980] mb I  I16..4: 31.7% 52.5% 15.8%
[libx264 @ 0x5d3d01cb8980] mb P  I16..4:  3.5%  7.3%  1.3%  P16..4: 17.5%  5.6%  5.1%  0.0%  0.0%    skip:59.7%
[libx264 @ 0x5d3d01cb8980] mb B  I16..4:  0.4%  0.5%  0.1%  B16..8: 19.8%  3.5%  1.3%  direct: 2.0%  skip:72.4%  L0:51.0% L1:46.0% BI: 3.0%
[libx264 @ 0x5d3d01cb8980] 8x8 transform intra:57.2% inter:35.1%
[libx264 @ 0x5d3d01cb8980] direct mvs  spatial:99.6